<p style="align:left;">
    <img src="https://upload.wikimedia.org/wikipedia/commons/6/64/Rome_banner_panorama.jpg" style="width:100%;"><br>
    <span style="font-size:80%;">Source: <a href="https://it.wikivoyage.org/wiki/Roma">https://it.wikivoyage.org/wiki/Roma</a></span>
</p>

<h1 align="center">The Battle of Neighborhoods</h1>
<h2 align="center">Final Notebook</h2>

<p>TABLE OF CONTENTS</p>
<p><a href="#sec1">1. GETTING DATA 1</a><br>
&nbsp;&nbsp;1.1 Rome's neighborhoods (Municipi)<br>
&nbsp;&nbsp;1.2 Rome's venues</p>
<p><a href="#sec2">2: FIRST STEP: cluster and selection neighborhood</a<br>
&nbsp;&nbsp;2.1 Neighborhoods analysis<br>
&nbsp;&nbsp;2.1 Clustering</p>    
<p><a href="#sec3">3. GETTING DATA 2</a<br>
&nbsp;&nbsp;3.1 Municipio 8's hotels<br>
&nbsp;&nbsp;3.2 Venues around hotels in Municipio 8</p>
<p><a href="#sec4">4: SECOND STEP: cluster and selection hotel</a<br>
&nbsp;&nbsp;4.1 Hotels analysis<br>
&nbsp;&nbsp;4.1 Clustering</p>  

<h1><a name="#sec1">1. GETTING DATA 1</a></h1>

<h3>1.1 Rome's neighborhoods (Municipi)</h3>

For this project, I need data information about Rome's neighborhoods (called Municipi). Data about neighborhoods are available in the Italian web portal of Open Data (<a href="http://www.datiopen.it/">http://www.datiopen.it/</a>): "Municipi di Roma". 
I downloaded the shape file that I elaborated it using QGIS (<a href="https://www.qgis.org/">https://www.qgis.org/</a>) to export a geojson file that associates for each neighborhood the latitude and the longitude of its centroid.
The resulting file is available here: <a href="http://5.249.144.7/donatellagubiani/Coursera/municipi_centroidi_js.geojson">municipi_centroidi_js.geojson</a>.

Before to show the data, I install and import all required libraries.

In [104]:
!pip install geopy
!pip install folium
!pip install geopy
!pip install yellowbrick

print('Libraries installed!')

     |████████████████████████████████| 20.2MB 6.7MB/s eta 0:00:01               | 5.9MB 7.6MB/s eta 0:00:02     |██████████████████▊             | 11.8MB 7.6MB/s eta 0:00:02     |███████████████████▊            | 12.4MB 7.6MB/s eta 0:00:02     |███████████████████████▏        | 14.6MB 6.7MB/s eta 0:00:01
  Found existing installation: numpy 1.12.0
    Uninstalling numpy-1.12.0:
      Successfully uninstalled numpy-1.12.0
Libraries installed!


In [105]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

from yellowbrick.cluster import KElbowVisualizer # library for optimization k value for kmeans

print('Libraries imported.')

Libraries imported.


So, I can download the geojson file, load it and then extract the required data (Neighborhood, Latitude, Longitude) to be included in a pandas's dataframe.

In [74]:
# download data
!wget -q -O 'rome_data.json' http://5.249.144.7/donatellagubiani/Coursera/municipi_centroidi_js.geojson
print('Data downloaded!')
# load geojson data
with open('rome_data.json') as json_data:
    rome = json.load(json_data)
# define the required dataframe columns
column_names = ['Neighborhood', 'Latitude', 'Longitude'] 
# instantiate the dataframe
neighborhoods_rome = pd.DataFrame(columns=column_names)
# populate the dataframe extracting the required values from the geojson
data_rome = rome['features']
data_rome[0]
for data in data_rome:
    neighborhood_name = data['properties']['municipio']     
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    neighborhoods_rome = neighborhoods_rome.append({'Neighborhood': 'Municipio ' +neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

# quick lock at data
neighborhoods_rome

Neighborhood   Latitude  Longitude
0    Municipio 1  41.898628  12.477950
1    Municipio 2  41.920704  12.501180
2    Municipio 3  41.996439  12.554324
3    Municipio 4  41.932162  12.591343
4    Municipio 5  41.889105  12.575565
5    Municipio 6  41.887550  12.687117
6    Municipio 7  41.839042  12.581899
7    Municipio 8  41.828667  12.529168
8    Municipio 9  41.757649  12.497813
9   Municipio 10  41.739390  12.363100
10  Municipio 11  41.830663  12.376779
11  Municipio 12  41.871017  12.344785
12  Municipio 13  41.910443  12.346112
13  Municipio 14  41.975664  12.345483
14  Municipio 15  42.029723  12.415673

Before to create a map, I determine the geographical coordinates of Rome.

In [75]:
address = 'Rome, Italy'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geographical coordinates of Rome (Italy) are {}, {}.'.format(latitude, longitude))

The geographical coordinates of Rome (Italy) are 41.8933203, 12.4829321.


And now I can show the map with the points that represent the neighborhood in Rome.

In [76]:
# create map of Rome using latitude and longitude values
map_rome = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, neighborhood in zip(neighborhoods_rome['Latitude'], neighborhoods_rome['Longitude'], neighborhoods_rome['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_rome)  
    
map_rome

<h3>1.2 GETTING DATA 1: Rome's venues</h3>

<p>Next, I need data about monuments and restaurants in Rome and I can obtain them working with the Foursquare API to explore the neighborhoods.<p>

In [77]:
# @hidden_cell
#
CLIENT_ID = 'OGIFOMCZEM2SUL2DP4BFA4LYHGX2KULMKCXM0WSIHKI0LAYD' # your Foursquare ID
CLIENT_SECRET = 'YDY4FRTT0V4DKBOTEVSQ34XOHC4KX5FZ2IASOQT2BDFITTDR' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
#print('Your credentails:')
#print('CLIENT_ID: ' + CLIENT_ID)
#print('CLIENT_SECRET:' + CLIENT_SECRET)

After setting my personal data for Foursquare, I can obtain the required data
Function to explore data (radius=500, limits=100) of all the neighborhoods in Rome.

I run the above function on each neighborhood and create a new dataframe called rome_venues. One note: checking the general distance between different neighborhoods, I decided to set the radius to 6000. As will be visible on the map, it allow a good coverage.

In [78]:
def getNearbyVenues(names, latitudes, longitudes, radius=500, limits=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limits)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [79]:
rome_venues = getNearbyVenues(names=neighborhoods_rome['Neighborhood'],
                              latitudes=neighborhoods_rome['Latitude'],
                              longitudes=neighborhoods_rome['Longitude'],
                              radius=6000)
#rome_venues.to_csv('rome_venues_6000_100.csv')
#rome_venues = pd.read_csv('rome_venues_6000_100.csv')
print(rome_venues.shape)
rome_venues.head()

(1027, 8)


Unnamed: 0 Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           0  Municipio 1              41.898628                12.47795   
1           1  Municipio 1              41.898628                12.47795   
2           2  Municipio 1              41.898628                12.47795   
3           3  Municipio 1              41.898628                12.47795   
4           4  Municipio 1              41.898628                12.47795   

                  Venue  Venue Latitude  Venue Longitude       Venue Category  
0              Pantheon       41.899133        12.476805  Monument / Landmark  
1    Pizza e Mozzarella       41.897598        12.479097          Pizza Place  
2   Il Panino Ingegnoso       41.899982        12.479195       Sandwich Place  
3  Piazza della Rotonda       41.899253        12.476779                Plaza  
4                Venchi       41.900042        12.480883       Ice Cream Shop

And I show them on a map.

In [80]:
# create map of Rome with all venues
map_romeV = map_rome # folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, venue, category, neighborhood in zip(rome_venues['Venue Latitude'], rome_venues['Venue Longitude'], rome_venues['Venue'], rome_venues['Venue Category'], rome_venues['Neighborhood']):
    label = '{} ({} in {})'.format(venue, category, neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='red',
        fill=True,
        fill_color='#cc3186',
        fill_opacity=0.7,
        parse_html=False).add_to(map_romeV)  
    
map_romeV

I check the categories and count elements for each category.

In [10]:
rome_venues.groupby(['Venue Category']).agg(['count'])

Unnamed: 0 Neighborhood Neighborhood Latitude  \
                              count        count                 count   
Venue Category                                                           
American Restaurant               3            3                     3   
Art Museum                        9            9                     9   
Asian Restaurant                  9            9                     9   
Athletics & Sports                5            5                     5   
Auditorium                        1            1                     1   
Automotive Shop                   1            1                     1   
BBQ Joint                         5            5                     5   
Bakery                           10           10                    10   
Bar                               5            5                     5   
Basketball Stadium                1            1                     1   
Beach                            15           15                    15   
Beer Bar                          1            1                     1   
Beer Garden                       4            4                     4   
Beer Store                        1            1                     1   
Big Box Store                     1            1                     1   
Bistro                            4            4                     4   
Bookstore                         5            5                     5   
Boutique                          7            7                     7   
Breakfast Spot                    2            2                     2   
Brewery                           2            2                     2   
Bridge                            1            1                     1   
Burger Joint                      6            6                     6   
Business Service                  1            1                     1   
Cafeteria                         2            2                     2   
Café                             50           50                    50   
Camera Store                      1            1                     1   
Campground                        3            3                     3   
Castle                            2            2                     2   
Chinese Restaurant               10           10                    10   
Church                            7            7                     7   
Clothing Store                    9            9                     9   
Cocktail Bar                      9            9                     9   
Coffee Shop                       3            3                     3   
Comfort Food Restaurant           1            1                     1   
Comic Shop                        2            2                     2   
Concert Hall                      1            1                     1   
Convenience Store                 1            1                     1   
Cosmetics Shop                    3            3                     3   
Courthouse                        1            1                     1   
Cuban Restaurant                  2            2                     2   
Cupcake Shop                      1            1                     1   
Deli / Bodega                     2            2                     2   
Department Store                  6            6                     6   
Dessert Shop                     13           13                    13   
Diner                             5            5                     5   
Discount Store                    2            2                     2   
Electronics Store                10           10                    10   
Event Space                       1            1                     1   
Farm                              4            4                     4   
Farmers Market                    1            1                     1   
Fast Food Restaurant             14           14                    14   
Film Studio                  

I check also the number of venues for each neighborhood.

In [11]:
rome_venues.groupby(['Neighborhood']).agg(['count'])

Unnamed: 0 Neighborhood Latitude Neighborhood Longitude Venue  \
                  count                 count                  count count   
Neighborhood                                                                 
Municipio 1         100                   100                    100   100   
Municipio 10         90                    90                     90    90   
Municipio 11         74                    74                     74    74   
Municipio 12         29                    29                     29    29   
Municipio 13         21                    21                     21    21   
Municipio 14         27                    27                     27    27   
Municipio 15         31                    31                     31    31   
Municipio 2         100                   100                    100   100   
Municipio 3          86                    86                     86    86   
Municipio 4         100                   100                    100   100   
Municipio 5         100                   100                    100   100   
Municipio 6          40                    40                     40    40   
Municipio 7         100                   100                    100   100   
Municipio 8         100                   100                    100   100   
Municipio 9          29                    29                     29    29   

             Venue Latitude Venue Longitude Venue Category  
                      count           count          count  
Neighborhood                                                
Municipio 1             100             100            100  
Municipio 10             90              90             90  
Municipio 11             74              74             74  
Municipio 12             29              29             29  
Municipio 13             21              21             21  
Municipio 14             27              27             27  
Municipio 15             31              31             31  
Municipio 2             100             100            100  
Municipio 3              86              86             86  
Municipio 4             100             100            100  
Municipio 5             100             100            100  
Municipio 6              40              40             40  
Municipio 7             100             100            100  
Municipio 8             100             100            100  
Municipio 9              29              29             29

From some tests, I verified that in this dataframe some important data are missing, as for the Colosseo. I try to increase the distance but it appears only with a big distance connected to a neighborhood that is not the close one. This because in any case the output of is limited to 100 venues, even if the parameter limits is set to 200. 

In [12]:
rome_venues_200 = getNearbyVenues(names=neighborhoods_rome['Neighborhood'],
                              latitudes=neighborhoods_rome['Latitude'],
                              longitudes=neighborhoods_rome['Longitude'],
                              radius=6000,
                              limits=200)
rome_venues_200.to_csv('rome_venues_6000_200.csv')
print(rome_venues_200.shape)
rome_venues_200.head()

Municipio 1
Municipio 2
Municipio 3
Municipio 4
Municipio 5
Municipio 6
Municipio 7
Municipio 8
Municipio 9
Municipio 10
Municipio 11
Municipio 12
Municipio 13
Municipio 14
Municipio 15
(1036, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Municipio 1              41.898628                12.47795   
1  Municipio 1              41.898628                12.47795   
2  Municipio 1              41.898628                12.47795   
3  Municipio 1              41.898628                12.47795   
4  Municipio 1              41.898628                12.47795   

                  Venue  Venue Latitude  Venue Longitude       Venue Category  
0              Pantheon       41.899133        12.476805  Monument / Landmark  
1    Pizza e Mozzarella       41.897598        12.479097          Pizza Place  
2   Il Panino Ingegnoso       41.899982        12.479195       Sandwich Place  
3  Piazza della Rotonda       41.899253        12.476779                Plaza  
4                Venchi       41.900042        12.480883       Ice Cream Shop

In [134]:
rome_venues.groupby(['Neighborhood']).agg(['count'])

Unnamed: 0 Neighborhood Latitude Neighborhood Longitude Venue  \
                  count                 count                  count count   
Neighborhood                                                                 
Municipio 1         100                   100                    100   100   
Municipio 10         90                    90                     90    90   
Municipio 11         74                    74                     74    74   
Municipio 12         29                    29                     29    29   
Municipio 13         21                    21                     21    21   
Municipio 14         27                    27                     27    27   
Municipio 15         31                    31                     31    31   
Municipio 2         100                   100                    100   100   
Municipio 3          86                    86                     86    86   
Municipio 4         100                   100                    100   100   
Municipio 5         100                   100                    100   100   
Municipio 6          40                    40                     40    40   
Municipio 7         100                   100                    100   100   
Municipio 8         100                   100                    100   100   
Municipio 9          29                    29                     29    29   

             Venue Latitude Venue Longitude Venue Category  
                      count           count          count  
Neighborhood                                                
Municipio 1             100             100            100  
Municipio 10             90              90             90  
Municipio 11             74              74             74  
Municipio 12             29              29             29  
Municipio 13             21              21             21  
Municipio 14             27              27             27  
Municipio 15             31              31             31  
Municipio 2             100             100            100  
Municipio 3              86              86             86  
Municipio 4             100             100            100  
Municipio 5             100             100            100  
Municipio 6              40              40             40  
Municipio 7             100             100            100  
Municipio 8             100             100            100  
Municipio 9              29              29             29

In [ ]:
<h1><a name="#sec2">2. FIRST STEP: cluster and selection neighborhood</a></h1>

Starting from this consideration, I decide to use this dataset to compare and evaluate which could be the better neighborhood, depending my preferences, where to reserve a hotel and so, I try to analyse data around hotels.

<h3>2.1 FIRST STEP: neighborhoods analysis</h3>

I started with some analysis on neighborhoods and their venues (numbers, most common, ...)

In [136]:
# one hot encoding
rome_onehot = pd.get_dummies(rome_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
rome_onehot['Neighborhood'] = rome_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [rome_onehot.columns[-1]] + list(rome_onehot.columns[:-1])
rome_onehot = rome_onehot[fixed_columns]

rome_onehot.head()

Neighborhood  American Restaurant  Art Museum  Asian Restaurant  \
0  Municipio 1                    0           0                 0   
1  Municipio 1                    0           0                 0   
2  Municipio 1                    0           0                 0   
3  Municipio 1                    0           0                 0   
4  Municipio 1                    0           0                 0   

   Athletics & Sports  Auditorium  Automotive Shop  BBQ Joint  Bakery  Bar  \
0                   0           0                0          0       0    0   
1                   0           0                0          0       0    0   
2                   0           0                0          0       0    0   
3                   0           0                0          0       0    0   
4                   0           0                0          0       0    0   

   Basketball Stadium  Beach  Beer Bar  Beer Garden  Beer Store  \
0                   0      0         0            0           0   
1                   0      0         0            0           0   
2                   0      0         0            0           0   
3                   0      0         0            0           0   
4                   0      0         0            0           0   

   Big Box Store  Bistro  Bookstore  Boutique  Breakfast Spot  Brewery  \
0              0       0          0         0               0        0   
1              0       0          0         0               0        0   
2              0       0          0         0               0        0   
3              0       0          0         0               0        0   
4              0       0          0         0               0        0   

   Bridge  Burger Joint  Business Service  Cafeteria  Café  Camera Store  \
0       0             0                 0          0     0             0   
1       0             0                 0          0     0             0   
2       0             0                 0          0     0             0   
3       0             0                 0          0     0             0   
4       0             0                 0          0     0             0   

   Campground  Castle  Chinese Restaurant  Church  Clothing Store  \
0           0       0                   0       0               0   
1           0       0                   0       0               0   
2           0       0                   0       0               0   
3           0       0                   0       0               0   
4           0       0                   0       0               0   

   Cocktail Bar  Coffee Shop  Comfort Food Restaurant  Comic Shop  \
0             0            0                        0           0   
1             0            0                        0           0   
2             0            0                        0           0   
3             0            0                        0           0   
4             0            0                        0           0   

   Concert Hall  Convenience Store  Cosmetics Shop  Courthouse  \
0             0                  0               0           0   
1             0                  0               0           0   
2             0                  0               0           0   
3             0                  0               0           0   
4             0                  0               0           0   

   Cuban Restaurant  Cupcake Shop  Deli / Bodega  Department Store  \
0                 0             0              0                 0   
1                 0             0              0                 0   
2                 0             0              0                 0   
3                 0             0              0                 0   
4                 0             0              0                 0   

   Dessert Shop  Diner  Discount Store  Electronics Store  Event Space  Farm  \
0             0      0               0                  0            0     0   
1    

In [137]:
rome_grouped = rome_onehot.groupby('Neighborhood').mean().reset_index()
rome_grouped

Neighborhood  American Restaurant  Art Museum  Asian Restaurant  \
0    Municipio 1             0.000000        0.03          0.000000   
1   Municipio 10             0.000000        0.00          0.022222   
2   Municipio 11             0.013514        0.00          0.013514   
3   Municipio 12             0.034483        0.00          0.000000   
4   Municipio 13             0.000000        0.00          0.000000   
5   Municipio 14             0.000000        0.00          0.074074   
6   Municipio 15             0.000000        0.00          0.064516   
7    Municipio 2             0.000000        0.04          0.000000   
8    Municipio 3             0.000000        0.00          0.000000   
9    Municipio 4             0.010000        0.00          0.010000   
10   Municipio 5             0.000000        0.01          0.000000   
11   Municipio 6             0.000000        0.00          0.025000   
12   Municipio 7             0.000000        0.00          0.000000   
13   Municipio 8             0.000000        0.01          0.000000   
14   Municipio 9             0.000000        0.00          0.000000   

    Athletics & Sports  Auditorium  Automotive Shop  BBQ Joint    Bakery  \
0             0.000000        0.00         0.000000   0.000000  0.010000   
1             0.011111        0.00         0.000000   0.000000  0.011111   
2             0.027027        0.00         0.000000   0.013514  0.000000   
3             0.034483        0.00         0.000000   0.000000  0.000000   
4             0.047619        0.00         0.000000   0.000000  0.047619   
5             0.000000        0.00         0.000000   0.000000  0.000000   
6             0.000000        0.00         0.000000   0.032258  0.000000   
7             0.000000        0.01         0.000000   0.000000  0.010000   
8             0.000000        0.00         0.000000   0.000000  0.000000   
9             0.000000        0.00         0.000000   0.000000  0.010000   
10            0.000000        0.00         0.000000   0.010000  0.010000   
11            0.000000        0.00         0.000000   0.000000  0.000000   
12            0.000000        0.00         0.000000   0.000000  0.010000   
13            0.000000        0.00         0.000000   0.010000  0.030000   
14            0.000000        0.00         0.034483   0.034483  0.000000   

         Bar  Basketball Stadium     Beach  Beer Bar  Beer Garden  Beer Store  \
0   0.000000            0.000000  0.000000      0.00     0.000000        0.00   
1   0.000000            0.000000  0.155556      0.00     0.000000        0.00   
2   0.013514            0.000000  0.000000      0.00     0.000000        0.00   
3   0.000000            0.000000  0.000000      0.00     0.000000        0.00   
4   0.000000            0.000000  0.000000      0.00     0.000000        0.00   
5   0.000000            0.000000  0.000000      0.00     0.000000        0.00   
6   0.000000            0.000000  0.000000      0.00     0.000000        0.00   
7   0.010000            0.000000  0.000000      0.00     0.000000        0.00   
8   0.011628            0.000000  0.000000      0.00     0.023256        0.00   
9   0.000000            0.000000  0.000000      0.00     0.020000        0.00   
10  0.020000            0.000000  0.000000      0.00     0.000000        0.01   
11  0.000000            0.000000  0.000000      0.00     0.000000        0.00   
12  0.000000            0.000000  0.000000      0.00     0.000000        0.00   
13  0.000000            0.000000  0.000000      0.01     0.000000        0.00   
14  0.000000            0.034483  0.034483      0.00     0.000000        0.00   

    Big Box Store    Bistro  Bookstore  Boutique  Breakfast Spot  Brewery  \
0        0.000000  0.010000   0.000000  0.020000            0.00     0.00   
1        0.000000  0.000000   0.000000  0.000000            0.00     0.00   
2        0.000000  0.013514   0.000000  0.000000            0.00     0.00   
3        0.000000  0.000000   0.000000  0.000

In [19]:
rome_grouped.shape

(15, 147)

In [138]:
num_top_venues = 5

for hood in rome_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = rome_grouped[rome_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Municipio 1----
                venue  freq
0               Plaza  0.14
1      Ice Cream Shop  0.09
2       Historic Site  0.09
3  Italian Restaurant  0.07
4      Sandwich Place  0.06


----Municipio 10----
                  venue  freq
0    Italian Restaurant  0.17
1                 Beach  0.16
2    Seafood Restaurant  0.04
3  Fast Food Restaurant  0.03
4           Pizza Place  0.03


----Municipio 11----
                venue  freq
0  Italian Restaurant  0.16
1         Pizza Place  0.11
2               Hotel  0.05
3                Park  0.04
4                Café  0.04


----Municipio 12----
                  venue  freq
0    Italian Restaurant  0.14
1                 Hotel  0.10
2           Supermarket  0.07
3     Electronics Store  0.07
4  Fast Food Restaurant  0.03


----Municipio 13----
                venue  freq
0  Italian Restaurant  0.24
1                Café  0.10
2    Department Store  0.10
3  Athletics & Sports  0.05
4                 Gym  0.05


----Municipio 14----
 

In [139]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [140]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = rome_grouped['Neighborhood']

for ind in np.arange(rome_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(rome_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head(15)

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0    Municipio 1                 Plaza        Ice Cream Shop   
1   Municipio 10    Italian Restaurant                 Beach   
2   Municipio 11    Italian Restaurant           Pizza Place   
3   Municipio 12    Italian Restaurant                 Hotel   
4   Municipio 13    Italian Restaurant                  Café   
5   Municipio 14    Italian Restaurant                 Hotel   
6   Municipio 15    Italian Restaurant  Gym / Fitness Center   
7    Municipio 2                 Plaza        Ice Cream Shop   
8    Municipio 3    Italian Restaurant           Pizza Place   
9    Municipio 4    Italian Restaurant           Pizza Place   
10   Municipio 5           Pizza Place        Ice Cream Shop   
11   Municipio 6        Clothing Store    Italian Restaurant   
12   Municipio 7    Italian Restaurant           Pizza Place   
13   Municipio 8           Pizza Place                  Park   
14   Municipio 9    Italian Restaurant                 Hotel   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0          Historic Site    Italian Restaurant        Sandwich Place   
1     Seafood Restaurant        Ice Cream Shop  Fast Food Restaurant   
2                  Hotel                  Café                  Park   
3            Supermarket     Electronics Store   American Restaurant   
4       Department Store                 Hotel        Sandwich Place   
5                    Pub      Asian Restaurant                  Pool   
6                  Hotel                  Café           Supermarket   
7                  Hotel         Historic Site   Monument / Landmark   
8                   Café            Steakhouse  Gym / Fitness Center   
9                   Café        Ice Cream Shop             Gastropub   
10                  Park    Italian Restaurant                 Hotel   
11  Fast Food Restaurant                  Café             Rest Area   
12                  Park                  Café        Ice Cream Shop   
13                  Café         Historic Site    Italian Restaurant   
14          Soccer Field                  Farm                  Café   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                 Wine Bar                Church              Fountain   
1            Historic Site                  Park           Pizza Place   
2                     Pool        Ice Cream Shop  Fast Food Restaurant   
3              Event Space        Sandwich Place           Pizza Place   
4   Furniture / Home Store            Steakhouse           Supermarket   
5              Supermarket         Deli / Bodega            Restaurant   
6               Restaurant                   Pub      Asian Restaurant   
7           Sandwich Place            Art Museum    Italian Restaurant   
8                    Hotel         Grocery Store           Supermarket   
9               Restaurant             Nightclub                  Park   
10            Cocktail Bar                  Café          Dessert Shop   
11       Electronics Store         Shopping Mall        Discount Store   
12           Historic Site              Wine Bar                 Hotel   
13          Ice Cream Shop                   Pub                Bakery   
14             Pizza Place             Rock Club  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
0    Monument / Landmark            Pizza Place  
1             Restaurant             Campground  
2   Gym / Fitness Center             Steakhouse  
3                   Park       Department Store  
4              Cafeteria   Gym / Fitness Center  
5         Clothing Store      Electronics Store  
6              BBQ Joint                   Pool  
7            Pizza Place         History Museum  
8      Electronics Store         Clothing Store  
9   Gym / Fitness Center            Beer Garden  
10             Gastropub   Gym / Fitness Center  
11            Restaurant         Ice Crea

<h3>2.2 FIRST STEP: Cluster Neighborhoods</h3>

I cluster the 15 neighborhoods (15) in 5 clusters.

In [141]:
# set number of clusters
kclusters = 5
rome_grouped_clustering = rome_grouped.drop('Neighborhood', 1)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(rome_grouped_clustering)
# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 0, 0, 3, 3, 1, 1, 2, 0, 0], dtype=int32)

In [142]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
rome_merged = neighborhoods_rome
# merge rome_grouped with rome_data to add latitude/longitude for each neighborhood
rome_merged = rome_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
rome_merged.head(15) # check the last columns!

Neighborhood   Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0    Municipio 1  41.898628  12.477950               2                 Plaza   
1    Municipio 2  41.920704  12.501180               2                 Plaza   
2    Municipio 3  41.996439  12.554324               0    Italian Restaurant   
3    Municipio 4  41.932162  12.591343               0    Italian Restaurant   
4    Municipio 5  41.889105  12.575565               0           Pizza Place   
5    Municipio 6  41.887550  12.687117               4        Clothing Store   
6    Municipio 7  41.839042  12.581899               0    Italian Restaurant   
7    Municipio 8  41.828667  12.529168               0           Pizza Place   
8    Municipio 9  41.757649  12.497813               3    Italian Restaurant   
9   Municipio 10  41.739390  12.363100               0    Italian Restaurant   
10  Municipio 11  41.830663  12.376779               0    Italian Restaurant   
11  Municipio 12  41.871017  12.344785               3    Italian Restaurant   
12  Municipio 13  41.910443  12.346112               3    Italian Restaurant   
13  Municipio 14  41.975664  12.345483               1    Italian Restaurant   
14  Municipio 15  42.029723  12.415673               1    Italian Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0         Ice Cream Shop         Historic Site    Italian Restaurant   
1         Ice Cream Shop                 Hotel         Historic Site   
2            Pizza Place                  Café            Steakhouse   
3            Pizza Place                  Café        Ice Cream Shop   
4         Ice Cream Shop                  Park    Italian Restaurant   
5     Italian Restaurant  Fast Food Restaurant                  Café   
6            Pizza Place                  Park                  Café   
7                   Park                  Café         Historic Site   
8                  Hotel          Soccer Field                  Farm   
9                  Beach    Seafood Restaurant        Ice Cream Shop   
10           Pizza Place                 Hotel                  Café   
11                 Hotel           Supermarket     Electronics Store   
12                  Café      Department Store                 Hotel   
13                 Hotel                   Pub      Asian Restaurant   
14  Gym / Fitness Center                 Hotel                  Café   

   5th Most Common Venue   6th Most Common Venue 7th Most Common Venue  \
0         Sandwich Place                Wine Bar                Church   
1    Monument / Landmark          Sandwich Place            Art Museum   
2   Gym / Fitness Center                   Hotel         Grocery Store   
3              Gastropub              Restaurant             Nightclub   
4                  Hotel            Cocktail Bar                  Café   
5              Rest Area       Electronics Store         Shopping Mall   
6         Ice Cream Shop           Historic Site              Wine Bar   
7     Italian Restaurant          Ice Cream Shop                   Pub   
8                   Café             Pizza Place             Rock Club   
9   Fast Food Restaurant           Historic Site                  Park   
10                  Park                    Pool        Ice Cream Shop   
11   American Restaurant             Event Space        Sandwich Place   
12        Sandwich Place  Furniture / Home Store            Steakhouse   
13                  Pool             Supermarket         Deli / Bodega   
14           Supermarket              Restaurant                   Pub   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0               Fountain   Monument / Landmark            Pizza Place  
1     Italian Restaurant           Pizza Place         History Museum  
2            Supermarket     Electronics Store         Clothing Store  
3                   Park  Gym / Fitness Center            Beer Garden  
4           Dessert Shop 

I create the map with clusters.

In [143]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(rome_merged['Latitude'], rome_merged['Longitude'], rome_merged['Neighborhood'], rome_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. 

In [46]:
# Cluster 1
rome_merged.loc[rome_merged['Cluster Labels'] == 0, rome_merged.columns[[0] + list(range(4, rome_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
2    Municipio 3    Italian Restaurant           Pizza Place   
3    Municipio 4    Italian Restaurant           Pizza Place   
4    Municipio 5           Pizza Place        Ice Cream Shop   
6    Municipio 7    Italian Restaurant           Pizza Place   
7    Municipio 8           Pizza Place                  Park   
9   Municipio 10    Italian Restaurant                 Beach   
10  Municipio 11    Italian Restaurant           Pizza Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2                   Café            Steakhouse  Gym / Fitness Center   
3                   Café        Ice Cream Shop             Gastropub   
4                   Park    Italian Restaurant                 Hotel   
6                   Park                  Café        Ice Cream Shop   
7                   Café         Historic Site    Italian Restaurant   
9     Seafood Restaurant        Ice Cream Shop  Fast Food Restaurant   
10                 Hotel                  Café                  Park   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2                  Hotel         Grocery Store           Supermarket   
3             Restaurant             Nightclub                  Park   
4           Cocktail Bar                  Café          Dessert Shop   
6          Historic Site              Wine Bar                 Hotel   
7         Ice Cream Shop                   Pub                Bakery   
9          Historic Site                  Park           Pizza Place   
10                  Pool        Ice Cream Shop  Fast Food Restaurant   

   9th Most Common Venue 10th Most Common Venue  
2      Electronics Store         Clothing Store  
3   Gym / Fitness Center            Beer Garden  
4              Gastropub   Gym / Fitness Center  
6           Burger Joint                    Gym  
7                  Hotel       Kebab Restaurant  
9             Restaurant             Campground  
10  Gym / Fitness Center             Steakhouse

In [47]:
# Cluster 2
rome_merged.loc[rome_merged['Cluster Labels'] == 1, rome_merged.columns[[0] + list(range(4, rome_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
13  Municipio 14    Italian Restaurant                 Hotel   
14  Municipio 15    Italian Restaurant  Gym / Fitness Center   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
13                   Pub      Asian Restaurant                  Pool   
14                 Hotel                  Café           Supermarket   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
13           Supermarket         Deli / Bodega            Restaurant   
14            Restaurant                   Pub      Asian Restaurant   

   9th Most Common Venue 10th Most Common Venue  
13        Clothing Store      Electronics Store  
14             BBQ Joint                   Pool

In [48]:
# Cluster 3
rome_merged.loc[rome_merged['Cluster Labels'] == 2, rome_merged.columns[[0] + list(range(4, rome_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Municipio 1                 Plaza        Ice Cream Shop   
1  Municipio 2                 Plaza        Ice Cream Shop   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Historic Site    Italian Restaurant        Sandwich Place   
1                 Hotel         Historic Site   Monument / Landmark   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0              Wine Bar                Church              Fountain   
1        Sandwich Place            Art Museum    Italian Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0   Monument / Landmark            Pizza Place  
1           Pizza Place         History Museum

In [49]:
# Cluster 4
rome_merged.loc[rome_merged['Cluster Labels'] == 3, rome_merged.columns[[0] + list(range(4, rome_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8    Municipio 9    Italian Restaurant                 Hotel   
11  Municipio 12    Italian Restaurant                 Hotel   
12  Municipio 13    Italian Restaurant                  Café   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8           Soccer Field                  Farm                  Café   
11           Supermarket     Electronics Store   American Restaurant   
12      Department Store                 Hotel        Sandwich Place   

     6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8              Pizza Place             Rock Club  Fast Food Restaurant   
11             Event Space        Sandwich Place           Pizza Place   
12  Furniture / Home Store            Steakhouse           Supermarket   

   9th Most Common Venue 10th Most Common Venue  
8                   Food             Food Court  
11                  Park       Department Store  
12             Cafeteria   Gym / Fitness Center

In [50]:
# Cluster 5
rome_merged.loc[rome_merged['Cluster Labels'] == 4, rome_merged.columns[[0] + list(range(4, rome_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
5  Municipio 6        Clothing Store    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
5  Fast Food Restaurant                  Café             Rest Area   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
5     Electronics Store         Shopping Mall        Discount Store   

  9th Most Common Venue 10th Most Common Venue  
5            Restaurant         Ice Cream Shop

In [ ]:
<h1><a name="#sec3">3. GETTING DATA 2</a></h1>

<h3>3.1 GETTING DATA 2: Hotels' Municipio 8</h3>

For the second second step of my analysis, I get hotels close to  Municipio 8. 
1) I select municipality 8
2) I execute the function on Municipio 8 (radius=5000, due to general distances in Rome)
3) I create a map

In [81]:
# selection Municipio 8
municipio8_data=neighborhoods_rome.loc[neighborhoods_rome['Neighborhood']=='Municipio 8']
print(municipio8_data.head())    
municipio8_latitude = municipio8_data['Latitude'].iloc[0]
municipio8_longitude = municipio8_data['Longitude'].iloc[0]

  Neighborhood   Latitude  Longitude
7  Municipio 8  41.828667  12.529168


In [82]:
# create the API request URL
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&categoryId={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            municipio8_latitude, 
            municipio8_longitude', 
            5000, 
            100,
            "4bf58dd8d48988d1fa931735") #id for Hotel from https://developer.foursquare.com/docs/resources/categories
# make the GET request
results = requests.get(url).json()
#print(results)
#with open('municipio8_hotels.json') as json_data:
#    results = json.load(json_data)
# assign relevant part of JSON to dataframe
column_names = ['Name', 'Latitude', 'Longitude', 'Category'] #'Address', 'Category'] 
# instantiate the dataframe
municipio8_hotels = pd.DataFrame(columns=column_names)
# populate the dataframe extracting the required values from the geojson
data_municipio8 = results['response']['groups'][0]['items']
data_municipio8[0]
for data in data_municipio8:
    hotel_name = data['venue']['name']     
    #hotel_address = data['venue']['location']['address']
    hotel_lat = data['venue']['location']['lat']
    hotel_lon = data['venue']['location']['lng']
    hotel_category = data['venue']['categories'][0]['shortName']
    municipio8_hotels = municipio8_hotels.append({'Name': hotel_name,
                                          'Latitude': hotel_lat,
                                          'Longitude': hotel_lon,
                                          #'Address': hotel_address,
                                          'Category': hotel_category}, ignore_index=True)
# quick lock at data
print(municipio8_hotels.shape)
print(municipio8_hotels.head())

(40, 4)
                    Name   Latitude  Longitude Category
0  Appia Park Hotel Roma  41.839210  12.551460    Hotel
1    Pulitzer Hotel Rome  41.847210  12.475833    Hotel
2  Barceló Aran Mantegna  41.852767  12.496737    Hotel
3     Hotel Orto di Roma  41.837235  12.510176    Hotel
4      Barceló Aran Park  41.821465  12.507848    Hotel


In [83]:
# create map of Rome with all italian restaurants
map_romeH = folium.Map(location=[municipio8_latitude, municipio8_longitude], zoom_start=12)

# add markers to map
for lat, lng, name, category in zip(municipio8_hotels['Latitude'], municipio8_hotels['Longitude'], municipio8_hotels['Name'], municipio8_hotels['Category']):
    label = '{} ({})'.format(name, category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='green',
        fill=True,
        fill_color='#31cc86',
        fill_opacity=0.7,
        parse_html=False).add_to(map_romeH)  
    
map_romeH

In [ ]:
<h3>3.2 GETTING DATA 2: Venues around hotels in Municipio 8</h3>

So, for each one hotel I get the closest venues (radius 1000).

In [84]:
hotels_venues = getNearbyVenues(names=municipio8_hotels['Name'],
                              latitudes=municipio8_hotels['Latitude'],
                              longitudes=municipio8_hotels['Longitude'],
                              radius=1000)
#hotels_venues.to_csv('hotels_venues_1000.csv')
#hotels_venues = pd.read_csv('hotels_venues_1000.csv')
print(hotels_venues.shape)
hotels_venues.head()

Appia Park Hotel Roma
Pulitzer Hotel Rome
Barceló Aran Mantegna
Hotel Orto di Roma
Barceló Aran Park
Kolping Casa Domitilla
Hotel il Piccolo Borgo
Hotel Villa EUR
Arco di Travertino Hotel Rome
Marini Park Hotel
Oly Hotel Rome
Villa Eur Parco dei Pini
Cinemusic Hotel
Ardeatina Park Hotel Rome
Hotel Capannelle
WH WarmtHotel
Hotel Caravel Rome
Hotel Romoli
American Palace Eur
Hotel dei Congressi
Aran Park Hotel
Hotel Antica Locanda Palmieri Rome
Locanda delle Corse Hotel
City Guest House
Hotel Casa Domitilla
Hotel Area
Hotel Piccolo Borgo
Meeting Hotel Rome
Hotel Cinecittà
B&B Hotel Roma Cinecittà
Eur Suite Hotel Rome
Waytostay
Residence Colombo 112
Hotel Giardino d'Europa
Hotel Palacavicchi Rome
The Strand Hotel
Dolce Vita affittacamere - Roma Cinecittà
Ariel.lorenzo Betancourt.sanchez
Twin Cities Hostel
Sheraton Pool
(1433, 8)


Unnamed: 0           Neighborhood  Neighborhood Latitude  \
0           0  Appia Park Hotel Roma               41.83921   
1           1  Appia Park Hotel Roma               41.83921   
2           2  Appia Park Hotel Roma               41.83921   
3           3  Appia Park Hotel Roma               41.83921   
4           4  Appia Park Hotel Roma               41.83921   

   Neighborhood Longitude                                Venue  \
0                12.55146                Appia Park Hotel Roma   
1                12.55146                            El Cubano   
2                12.55146  Grani Di Sale - Ristorante Pizzeria   
3                12.55146                 La Taverna del Parco   
4                12.55146              Ristorante San Tarcisio   

   Venue Latitude  Venue Longitude      Venue Category  
0       41.839210        12.551460               Hotel  
1       41.834021        12.555919    Cuban Restaurant  
2       41.844693        12.549148         Pizza Place  
3       41.844194        12.551960          Steakhouse  
4       41.842971        12.541759  Italian Restaurant

In [85]:
# create map of Rome with hotels and venues
map_romeHV = map_romeH #folium.Map(location=[municipio8_latitude, municipio8_longitude], zoom_start=13)

# add markers to map
for lat, lng, name, category in zip(hotels_venues['Venue Latitude'], hotels_venues['Venue Longitude'], hotels_venues['Venue'], hotels_venues['Venue Category']):
    label = '{} ({})'.format(name, category)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#31cc86',
        fill_opacity=0.7,
        parse_html=False).add_to(map_romeHV)  
    
map_romeHV

A quick check.

In [86]:
hotels_venues.groupby(['Neighborhood']).agg(['count'])

Unnamed: 0 Neighborhood Latitude  \
                                               count                 count   
Neighborhood                                                                 
American Palace Eur                               32                    32   
Appia Park Hotel Roma                             20                    20   
Aran Park Hotel                                   11                    11   
Arco di Travertino Hotel Rome                     67                    67   
Ardeatina Park Hotel Rome                          6                     6   
Ariel.lorenzo Betancourt.sanchez                  80                    80   
B&B Hotel Roma Cinecittà                          13                    13   
Barceló Aran Mantegna                             44                    44   
Barceló Aran Park                                 11                    11   
Cinemusic Hotel                                   14                    14   
City Guest House                                  63                    63   
Dolce Vita affittacamere - Roma Cinecittà         67                    67   
Eur Suite Hotel Rome                              20                    20   
Hotel Antica Locanda Palmieri Rome                17                    17   
Hotel Area                                        60                    60   
Hotel Capannelle                                  18                    18   
Hotel Caravel Rome                                51                    51   
Hotel Casa Domitilla                              28                    28   
Hotel Cinecittà                                   25                    25   
Hotel Giardino d'Europa                           11                    11   
Hotel Orto di Roma                                16                    16   
Hotel Palacavicchi Rome                           11                    11   
Hotel Piccolo Borgo                               17                    17   
Hotel Romoli                                      55                    55   
Hotel Villa EUR                                   23                    23   
Hotel dei Congressi                               64                    64   
Hotel il Piccolo Borgo                            13                    13   
Kolping Casa Domitilla                            27                    27   
Locanda delle Corse Hotel                         12                    12   
Marini Park Hotel                                  5                     5   
Meeting Hotel Rome                                15                    15   
Oly Hotel Rome                                    79                    79   
Pulitzer Hotel Rome                               68                    68   
Residence Colombo 112                             59                    59   
Sheraton Pool                                     27                    27   
The Strand Hotel                                  64                    64   
Twin Cities Hostel                                83                    83   
Villa Eur Parco dei Pini                          21                    21   
WH WarmtHotel                                     20                    20   
Waytostay                                         96                    96   

                                          Neighborhood Longitude Venue  \
                                                           count count   
Neighborhood                                                             
American Palace Eur                                           32    32   
Appia Park Hotel Roma                                         20    20   
Aran Park Hotel                                               11    11   
Arco di Travertino Hotel Rome                                 67    67   
Ardeatina Park Hotel Rome                                      6     6   
Ariel.lorenzo Betancourt.sanchez                              80    80   
B&B Hotel Roma Cineci

<h1><a name="#sec4">4. SECOND STEP: Clustering and selection hotel</a></h1>

<h3>4.1 SECOND STEP: Hotels analysis</h3>  

I started with some analysis on hotels and their venues (numbers, most common, ...)

In [87]:
# one hot encoding
hotels_onehot = pd.get_dummies(hotels_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
hotels_onehot['Neighborhood'] = hotels_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [hotels_onehot.columns[-1]] + list(hotels_onehot.columns[:-1])
hotels_onehot = hotels_onehot[fixed_columns]

print(hotels_onehot.shape)
hotels_onehot.head()

(1433, 136)


Neighborhood  Airport  American Restaurant  Art Museum  \
0  Appia Park Hotel Roma        0                    0           0   
1  Appia Park Hotel Roma        0                    0           0   
2  Appia Park Hotel Roma        0                    0           0   
3  Appia Park Hotel Roma        0                    0           0   
4  Appia Park Hotel Roma        0                    0           0   

   Asian Restaurant  Athletics & Sports  Bakery  Bar  Basketball Court  \
0                 0                   0       0    0                 0   
1                 0                   0       0    0                 0   
2                 0                   0       0    0                 0   
3                 0                   0       0    0                 0   
4                 0                   0       0    0                 0   

   Basketball Stadium  Bed & Breakfast  Beer Bar  Beer Garden  Bistro  \
0                   0                0         0            0       0   
1                   0                0         0            0       0   
2                   0                0         0            0       0   
3                   0                0         0            0       0   
4                   0                0         0            0       0   

   Boarding House  Bookstore  Boutique  Breakfast Spot  Brewery  Burger Joint  \
0               0          0         0               0        0             0   
1               0          0         0               0        0             0   
2               0          0         0               0        0             0   
3               0          0         0               0        0             0   
4               0          0         0               0        0             0   

   Bus Station  Butcher  Cafeteria  Café  Camera Store  Chinese Restaurant  \
0            0        0          0     0             0                   0   
1            0        0          0     0             0                   0   
2            0        0          0     0             0                   0   
3            0        0          0     0             0                   0   
4            0        0          0     0             0                   0   

   Clothing Store  Cocktail Bar  Coffee Shop  College Cafeteria  College Gym  \
0               0             0            0                  0            0   
1               0             0            0                  0            0   
2               0             0            0                  0            0   
3               0             0            0                  0            0   
4               0             0            0                  0            0   

   Comic Shop  Cosmetics Shop  Cuban Restaurant  Cultural Center  \
0           0               0                 0                0   
1           0               0                 1                0   
2           0               0                 0                0   
3           0               0                 0                0   
4           0               0                 0                0   

   Cupcake Shop  Dance Studio  Department Store  Dessert Shop  Diner  \
0             0             0                 0             0      0   
1             0             0                 0             0      0   
2             0             0                 0             0      0   
3             0             0                 0             0      0   
4             0             0                 0             0      0   

   Discount Store  Dive Bar  Electronics Store  Farmers Market  \
0               0         0                  0               0   
1               0         0                  0               0   
2               0         0                  0               0   
3               0         0                  0               0   
4               0         0                  0               0   

   Fast Food Restaurant  Film S

In [88]:
hotels_grouped = hotels_onehot.groupby('Neighborhood').mean().reset_index()
print(hotels_grouped.shape)
hotels_grouped

(40, 136)


Neighborhood   Airport  American Restaurant  \
0                         American Palace Eur  0.000000             0.000000   
1                       Appia Park Hotel Roma  0.000000             0.000000   
2                             Aran Park Hotel  0.000000             0.000000   
3               Arco di Travertino Hotel Rome  0.000000             0.000000   
4                   Ardeatina Park Hotel Rome  0.000000             0.000000   
5            Ariel.lorenzo Betancourt.sanchez  0.000000             0.000000   
6                    B&B Hotel Roma Cinecittà  0.000000             0.000000   
7                       Barceló Aran Mantegna  0.000000             0.022727   
8                           Barceló Aran Park  0.000000             0.000000   
9                             Cinemusic Hotel  0.000000             0.000000   
10                           City Guest House  0.015873             0.000000   
11  Dolce Vita affittacamere - Roma Cinecittà  0.000000             0.000000   
12                       Eur Suite Hotel Rome  0.000000             0.000000   
13         Hotel Antica Locanda Palmieri Rome  0.000000             0.000000   
14                                 Hotel Area  0.000000             0.000000   
15                           Hotel Capannelle  0.000000             0.000000   
16                         Hotel Caravel Rome  0.000000             0.000000   
17                       Hotel Casa Domitilla  0.000000             0.000000   
18                            Hotel Cinecittà  0.000000             0.000000   
19                    Hotel Giardino d'Europa  0.000000             0.000000   
20                         Hotel Orto di Roma  0.000000             0.000000   
21                    Hotel Palacavicchi Rome  0.000000             0.000000   
22                        Hotel Piccolo Borgo  0.000000             0.000000   
23                               Hotel Romoli  0.000000             0.000000   
24                            Hotel Villa EUR  0.000000             0.000000   
25                        Hotel dei Congressi  0.000000             0.000000   
26                     Hotel il Piccolo Borgo  0.000000             0.000000   
27                     Kolping Casa Domitilla  0.000000             0.000000   
28                  Locanda delle Corse Hotel  0.000000             0.000000   
29                          Marini Park Hotel  0.000000             0.000000   
30                         Meeting Hotel Rome  0.000000             0.000000   
31                             Oly Hotel Rome  0.000000             0.012658   
32                        Pulitzer Hotel Rome  0.000000             0.000000   
33                      Residence Colombo 112  0.000000             0.000000   
34                              Sheraton Pool  0.000000             0.000000   
35                           The Strand Hotel  0.015625             0.000000   
36                         Twin Cities Hostel  0.000000             0.012048   
37                   Villa Eur Parco dei Pini  0.000000             0.000000   
38                              WH WarmtHotel  0.000000             0.000000   
39                                  Waytostay  0.000000             0.000000   

    Art Museum  Asian Restaurant  Athletics & Sports    Bakery       Bar  \
0      0.03125          0.000000            0.000000  0.031250  0.000000   
1      0.00000          0.000000            0.000000  0.000000  0.000000   
2      0.00000          0.000000            0.000000  0.000000  0.000000   
3      0.00000          0.000000            0.000000  0.014925  0.029851   
4      0.00000          0.000000            0.000000  0.000000  0.000000   
5      0.00000          0.025000            0.000000  0.012500  0.012500   
6      0.00000          0.000000            0.000000  0.076923  0.000000   
7      0.00000          0.000000            0.000000  0.022727  0.000000   
8      0.00000          0.000000            0.000000  0.000000  0.00

In [89]:
# TOP 5
num_top_venues = 5

for hood in hotels_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = hotels_grouped[hotels_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----American Palace Eur----
                venue  freq
0               Hotel  0.12
1  Italian Restaurant  0.12
2                Café  0.09
3                 Gym  0.06
4      Ice Cream Shop  0.03


----Appia Park Hotel Roma----
                  venue  freq
0                 Hotel  0.15
1                  Café  0.10
2  Gym / Fitness Center  0.10
3           Pizza Place  0.05
4     Food & Drink Shop  0.05


----Aran Park Hotel----
                  venue  freq
0           Pizza Place  0.18
1                  Café  0.18
2                 Plaza  0.09
3  Gym / Fitness Center  0.09
4   Sporting Goods Shop  0.09


----Arco di Travertino Hotel Rome----
                  venue  freq
0           Pizza Place  0.10
1    Italian Restaurant  0.09
2                   Pub  0.06
3        Ice Cream Shop  0.04
4  Fast Food Restaurant  0.04


----Ardeatina Park Hotel Rome----
                   venue  freq
0     Italian Restaurant  0.33
1             Steakhouse  0.33
2                  Hotel  0.17
3    S

In [90]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [92]:
# TOP 10
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
hotels_venues_sorted = pd.DataFrame(columns=columns)
hotels_venues_sorted['Neighborhood'] = hotels_grouped['Neighborhood']

for ind in np.arange(hotels_grouped.shape[0]):
    hotels_venues_sorted.iloc[ind, 1:] = return_most_common_venues(hotels_grouped.iloc[ind, :], num_top_venues)

hotels_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0            American Palace Eur    Italian Restaurant                 Hotel   
1          Appia Park Hotel Roma                 Hotel                  Café   
2                Aran Park Hotel           Pizza Place                  Café   
3  Arco di Travertino Hotel Rome           Pizza Place    Italian Restaurant   
4      Ardeatina Park Hotel Rome    Italian Restaurant            Steakhouse   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Café                   Gym        History Museum   
1  Gym / Fitness Center          Tennis Court     Food & Drink Shop   
2                 Hotel  Gym / Fitness Center                 Plaza   
3                   Pub        Ice Cream Shop  Fast Food Restaurant   
4                 Hotel   Sporting Goods Shop         Women's Store   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0           Planetarium            Pizza Place           Music Venue   
1          Burger Joint       Football Stadium            Steakhouse   
2                  Park  Outdoors & Recreation           Supermarket   
3           Supermarket                   Café    Chinese Restaurant   
4        Farmers Market            Fish Market     Fish & Chips Shop   

  9th Most Common Venue 10th Most Common Venue  
0   Moroccan Restaurant          Metro Station  
1       Bed & Breakfast      Martial Arts Dojo  
2   Sporting Goods Shop          Women's Store  
3                  Park           Cupcake Shop  
4           Film Studio   Fast Food Restaurant

<h3>4.2 SECOND STEP: Clustering</h3>  

I create the clusters using k=5.

In [120]:
# set number of clusters
kclusters = 5
hotels_grouped_clustering = hotels_grouped.drop('Neighborhood', 1)
# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(hotels_grouped_clustering)
# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([3, 3, 4, 0, 1, 0, 3, 0, 4, 3], dtype=int32)

In [125]:
# add clustering labels
hotels_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
hotels_merged = municipio8_hotels
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
hotels_merged = hotels_merged.join(hotels_venues_sorted.set_index('Neighborhood'), on='Name')
hotels_merged.head() # check the last columns!

Name   Latitude  Longitude Category  Cluster Labels  \
0  Appia Park Hotel Roma  41.839210  12.551460    Hotel               3   
1    Pulitzer Hotel Rome  41.847210  12.475833    Hotel               0   
2  Barceló Aran Mantegna  41.852767  12.496737    Hotel               0   
3     Hotel Orto di Roma  41.837235  12.510176    Hotel               2   
4      Barceló Aran Park  41.821465  12.507848    Hotel               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                 Hotel                  Café  Gym / Fitness Center   
1    Italian Restaurant                  Café           Pizza Place   
2           Pizza Place    Italian Restaurant                  Café   
3                  Café    Italian Restaurant                  Park   
4           Pizza Place                  Café                 Hotel   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Tennis Court     Food & Drink Shop          Burger Joint   
1                 Hotel        Ice Cream Shop        Sandwich Place   
2                 Hotel           Supermarket                 Plaza   
3                 Hotel   Sporting Goods Shop                   Pub   
4  Gym / Fitness Center                 Plaza                  Park   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0       Football Stadium            Steakhouse       Bed & Breakfast   
1                 Bistro           Supermarket             Hotel Bar   
2    Japanese Restaurant        Ice Cream Shop             Multiplex   
3            Gas Station  Fast Food Restaurant        Farmers Market   
4  Outdoors & Recreation           Supermarket   Sporting Goods Shop   

  10th Most Common Venue  
0      Martial Arts Dojo  
1                  Plaza  
2    Monument / Landmark  
3      Fish & Chips Shop  
4          Women's Store

In [127]:
# create map
map2_clusters = folium.Map(location=[municipio8_latitude, municipio8_longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(hotels_merged['Latitude'], hotels_merged['Longitude'], hotels_merged['Name'], hotels_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map2_clusters)
       
map2_clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. 

In [128]:
# Cluster 1
hotels_merged.loc[hotels_merged['Cluster Labels'] == 0, hotels_merged.columns[[0] + list(range(4, hotels_merged.shape[1]))]]

Name  Cluster Labels  \
1                         Pulitzer Hotel Rome               0   
2                       Barceló Aran Mantegna               0   
8               Arco di Travertino Hotel Rome               0   
10                             Oly Hotel Rome               0   
16                         Hotel Caravel Rome               0   
17                               Hotel Romoli               0   
19                        Hotel dei Congressi               0   
23                           City Guest House               0   
25                                 Hotel Area               0   
28                            Hotel Cinecittà               0   
31                                  Waytostay               0   
32                      Residence Colombo 112               0   
35                           The Strand Hotel               0   
36  Dolce Vita affittacamere - Roma Cinecittà               0   
37           Ariel.lorenzo Betancourt.sanchez               0   
38                         Twin Cities Hostel               0   
39                              Sheraton Pool               0   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
1     Italian Restaurant                  Café           Pizza Place   
2            Pizza Place    Italian Restaurant                  Café   
8            Pizza Place    Italian Restaurant                   Pub   
10                  Café    Italian Restaurant           Pizza Place   
16    Italian Restaurant                  Café           Pizza Place   
17           Pizza Place    Italian Restaurant                 Plaza   
19                  Café                 Hotel             Nightclub   
23    Italian Restaurant                  Café           Pizza Place   
25    Italian Restaurant                  Café                 Hotel   
28           Film Studio                  Café           Bus Station   
31           Pizza Place    Italian Restaurant        Ice Cream Shop   
32    Italian Restaurant                  Café           Pizza Place   
35    Italian Restaurant                  Café        Ice Cream Shop   
36           Pizza Place                  Café        Ice Cream Shop   
37                  Café    Italian Restaurant           Pizza Place   
38    Italian Restaurant                  Café           Pizza Place   
39             Nightclub                  Café                   Gym   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
1                  Hotel        Ice Cream Shop        Sandwich Place   
2                  Hotel           Supermarket                 Plaza   
8         Ice Cream Shop  Fast Food Restaurant           Supermarket   
10        Ice Cream Shop           Supermarket                 Hotel   
16                 Hotel                  Park                 Plaza   
17                 Hotel        Ice Cream Shop  Gym / Fitness Center   
19        Ice Cream Shop            Restaurant    Italian Restaurant   
23        Ice Cream Shop                   Pub        Clothing Store   
25           Pizza Place           Supermarket             Hotel Bar   
28           Coffee Shop         Shopping Mall        Cosmetics Shop   
31                   Pub                   Bar  Fast Food Restaurant   
32                 Plaza    Chinese Restaurant                 Hotel   
35           Pizza Place           Supermarket            Restaurant   
36        Clothing Store  Fast Food Restaurant    Italian Restaurant   
37                 Hotel        Ice Cream Shop                Bistro   
38        Ice Cream Shop                 Hotel           Supermarket   
39    Italian Restaurant           Supermarket           Salad Place   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
1                 Bistro           Supermarket             Hotel Bar   
2    Japanese Restaurant        Ice Cream Shop             Multiplex   
8                   Café    Chinese Restaurant              

In [129]:
# Cluster 2
hotels_merged.loc[hotels_merged['Cluster Labels'] == 1, hotels_merged.columns[[0] + list(range(4, hotels_merged.shape[1]))]]

Name  Cluster Labels 1st Most Common Venue  \
13  Ardeatina Park Hotel Rome               1    Italian Restaurant   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
13            Steakhouse                 Hotel   Sporting Goods Shop   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
13         Women's Store        Farmers Market           Fish Market   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
13     Fish & Chips Shop           Film Studio   Fast Food Restaurant

In [130]:
# Cluster 3
hotels_merged.loc[hotels_merged['Cluster Labels'] == 2, hotels_merged.columns[[0] + list(range(4, hotels_merged.shape[1]))]]

Name  Cluster Labels 1st Most Common Venue  \
3                   Hotel Orto di Roma               2                  Café   
9                    Marini Park Hotel               2                 Hotel   
21  Hotel Antica Locanda Palmieri Rome               2                  Café   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
3     Italian Restaurant                  Park                 Hotel   
9   Fast Food Restaurant    Italian Restaurant           Gas Station   
21    Italian Restaurant                  Park                 Hotel   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
3    Sporting Goods Shop                   Pub           Gas Station   
9                   Café     Food & Drink Shop           Fish Market   
21         Luggage Store                   Pub   Sporting Goods Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
3   Fast Food Restaurant        Farmers Market      Fish & Chips Shop  
9      Fish & Chips Shop           Film Studio         Farmers Market  
21  Fast Food Restaurant           Gas Station      Fish & Chips Shop

In [131]:
# Cluster 4
hotels_merged.loc[hotels_merged['Cluster Labels'] == 3, hotels_merged.columns[[0] + list(range(4, hotels_merged.shape[1]))]]

Name  Cluster Labels 1st Most Common Venue  \
0       Appia Park Hotel Roma               3                 Hotel   
5      Kolping Casa Domitilla               3                 Hotel   
6      Hotel il Piccolo Borgo               3                 Hotel   
7             Hotel Villa EUR               3                 Hotel   
11   Villa Eur Parco dei Pini               3                 Hotel   
12            Cinemusic Hotel               3                 Hotel   
14           Hotel Capannelle               3                 Hotel   
18        American Palace Eur               3    Italian Restaurant   
22  Locanda delle Corse Hotel               3                 Hotel   
24       Hotel Casa Domitilla               3                 Hotel   
26        Hotel Piccolo Borgo               3                 Hotel   
27         Meeting Hotel Rome               3                 Hotel   
29   B&B Hotel Roma Cinecittà               3                 Hotel   
33    Hotel Giardino d'Europa               3                 Hotel   
34    Hotel Palacavicchi Rome               3                 Hotel   

     2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
0                     Café    Gym / Fitness Center          Tennis Court   
5       Italian Restaurant                    Café           Supermarket   
6       Italian Restaurant               Pet Store           Music Venue   
7                     Café      Italian Restaurant           Pizza Place   
11                    Café             Pizza Place    Italian Restaurant   
12                    Café             Bus Station          Tennis Court   
14                    Café    Gym / Fitness Center         Historic Site   
18                   Hotel                    Café                   Gym   
22      Italian Restaurant               Gastropub                  Café   
24      Italian Restaurant                    Café           Supermarket   
26      Italian Restaurant  Furniture / Home Store               Brewery   
27              Shoe Store               Pet Store      Department Store   
29            Tennis Court             Pizza Place              Dive Bar   
33             Supermarket                    Pool        Clothing Store   
34  Furniture / Home Store   Performing Arts Venue                   Pub   

     5th Most Common Venue  6th Most Common Venue  7th Most Common Venue  \
0        Food & Drink Shop           Burger Joint       Football Stadium   
5                    Plaza         Ice Cream Shop    Monument / Landmark   
6                     Café          Train Station    Fried Chicken Joint   
7            Women's Store            Planetarium                 Bakery   
11           Women's Store                 Bakery     Basketball Stadium   
12             Pizza Place               Dive Bar             Restaurant   
14      Italian Restaurant            Golf Course      Martial Arts Dojo   
18          History Museum            Planetarium            Pizza Place   
22  Furniture / Home Store                    Pub                Stables   
24           Historic Site                  Plaza         Ice Cream Shop   
26    Gym / Fitness Center  Performing Arts Venue  Outdoors & Recreation   
27   Performing Arts Venue                   Pool         Clothing Store   
29    Fast Food Restaurant             Restaurant                   Café   
33                    Café             Shoe Store    Fried Chicken Joint   
34   Outdoors & Recreation             Restaurant           Cupcake Shop   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0             Steakhouse       Bed & Breakfast      Martial Arts Dojo  
5                   Park         Historic Site     Chinese Restaurant  
6                   Pool           Coffee Shop            Supermarket  
7     Basketball Stadium    Chinese Restaurant             Comic Shop  
11    Chinese Restaurant            Comic Shop                    Gym  
12    Seafood Restaura

In [132]:
# Cluster 5
hotels_merged.loc[hotels_merged['Cluster Labels'] == 4, hotels_merged.columns[[0] + list(range(4, hotels_merged.shape[1]))]]

Name  Cluster Labels 1st Most Common Venue  \
4      Barceló Aran Park               4           Pizza Place   
15         WH WarmtHotel               4           Pizza Place   
20       Aran Park Hotel               4           Pizza Place   
30  Eur Suite Hotel Rome               4           Pizza Place   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
4                   Café                 Hotel  Gym / Fitness Center   
15                  Café                 Hotel           Supermarket   
20                  Café                 Hotel  Gym / Fitness Center   
30                  Café                 Hotel           Supermarket   

   5th Most Common Venue 6th Most Common Venue  7th Most Common Venue  \
4                  Plaza                  Park  Outdoors & Recreation   
15       Cultural Center          Dessert Shop             Restaurant   
20                 Plaza                  Park  Outdoors & Recreation   
30       Cultural Center          Dessert Shop             Restaurant   

   8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
4            Supermarket   Sporting Goods Shop          Women's Store  
15    Chinese Restaurant               Butcher                 Market  
20           Supermarket   Sporting Goods Shop          Women's Store  
30    Chinese Restaurant               Butcher                 Market